# **Bitcoin price forecasting - GeneralizedLinearRegression**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author
Corsi Danilo - corsi.1742375@studenti.uniroma1.it



## Global constants, dependencies, libraries and tools

In [1]:
# GDrive root
GDRIVE_DIR = "/content/drive"

# Dataset
GDRIVE_DATASET_OUTPUT_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/datasets/output"
GDRIVE_DATASET_NAME = "bitcoin_blockchain_data_30min"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_NAME + "_train_valid"
GDRIVE_DATASET_NAME_EXT_ENG  = "/" + GDRIVE_DATASET_NAME_ENG + ".parquet"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_OUTPUT_DIR + GDRIVE_DATASET_NAME_EXT_ENG

# Features
GDRIVE_FEATURES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/features"
GDRIVE_ALL_FEATURES_NAME = "all_features"
GDRIVE_MORE_REL_FEATURES_NAME = "more_rel_features"
GDRIVE_LESS_REL_FEATURES_NAME = "less_rel_features"
GDRIVE_ALL_FEATURES_NAME_EXT = "/" + GDRIVE_ALL_FEATURES_NAME + ".json"
GDRIVE_MORE_REL_FEATURES_NAME_EXT = "/" + GDRIVE_MORE_REL_FEATURES_NAME + ".json"
GDRIVE_LESS_REL_FEATURES_NAME_EXT = "/" + GDRIVE_LESS_REL_FEATURES_NAME + ".json"
GDRIVE_ALL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_ALL_FEATURES_NAME_EXT
GDRIVE_MORE_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_MORE_REL_FEATURES_NAME_EXT
GDRIVE_LESS_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_LESS_REL_FEATURES_NAME_EXT

# Others
JAVA_HOME = "/usr/lib/jvm/java-8-openjdk-amd64"
MODEL_NAME = "GeneralizedLinearRegression"
SLOW_OPERATION = True

In [2]:
# Point Colaboratory to our Google Drive
from google.colab import drive

# Define GDrive paths
drive.mount(GDRIVE_DIR, force_remount=True)

Mounted at /content/drive


In [3]:
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

In [4]:
# Install Spark and related dependencies
!pip install pyspark

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.8/310.8 MB 4.9 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyspark: filename=pyspark-3.4.1-py2.py3-none-any.whl size=311285388 sha256=469615c59c7abdf4c1042a1ff2e138c2f0917f1934a0f2aa5b1f29b821ba0597
  Stored in directory: /root/.cache/pip/wheels/0d/77/a3/ff2f74cc9ab41f8f594dabf0579c2a7c6de920d584206e0834
Successfully built pyspark


## Import files

In [5]:
GDRIVE_UTILITIES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/utilities"

import sys
sys.path.append(GDRIVE_UTILITIES_DIR)

from imports import *
import utilities, parameters

importlib.reload(utilities)
importlib.reload(parameters)

<module 'parameters' from '/content/drive/MyDrive/BDC/project/utilities/parameters.py'>

## Create the pyspark session

In [6]:
# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '4G').\
                set('spark.driver.memory', '45G').\
                set('spark.driver.maxResultSize', '10G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPriceForecasting").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

## Loading dataset

In [7]:
# Load datasets into pyspark dataset objects
df = spark.read.load(GDRIVE_DATASET_NAME_ENG,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

In [8]:
def dataset_info(dataset):
  dataset.show(3)

  # Get the number of rows
  num_rows = dataset.count()

  # Get the number of columns
  num_columns = len(dataset.columns)

  # Print the shape of the dataset
  print("Shape:", (num_rows, num_columns))

  # Print the schema of the dataset
  dataset.printSchema()

In [9]:
if SLOW_OPERATION:
  dataset_info(df)

+-------------------+---+------------------+--------------+-------------------+--------------+------------------+------------------+--------------------+------------------------+-----------------+-------------------+------------------+--------------------+------------------+------------------+--------------------------------+--------------------+------------------+------------------+------------------+------------------+------------------+------------------+
|          timestamp| id|      market-price|total-bitcoins|         market-cap|  trade-volume|       blocks-size|    avg-block-size|n-transactions-total|n-transactions-per-block|        hash-rate|         difficulty|    miners-revenue|transaction-fees-usd|n-unique-addresses|    n-transactions|estimated-transaction-volume-usd|      rate-of-change|        sma-5-days|        sma-7-days|       sma-10-days|       sma-20-days|       sma-50-days|      sma-100-days|
+-------------------+---+------------------+--------------+---------------

## Loading features

In [10]:
# Set the features label
FEATURES_LABEL = "features"

# Set the target variable
TARGET_VAL = 'market-price'

In [11]:
# Loading correlation matrix features
with open(GDRIVE_ALL_FEATURES, "r") as f:
    all_features = json.load(f)
print(all_features)

['total-bitcoins', 'market-cap', 'trade-volume', 'blocks-size', 'avg-block-size', 'n-transactions-total', 'n-transactions-per-block', 'hash-rate', 'difficulty', 'miners-revenue', 'transaction-fees-usd', 'n-unique-addresses', 'n-transactions', 'estimated-transaction-volume-usd', 'rate-of-change', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'sma-20-days', 'sma-50-days', 'sma-100-days']


In [12]:
# Loading correlation matrix features
with open(GDRIVE_MORE_REL_FEATURES, "r") as f:
    more_rel_features = json.load(f)
print(more_rel_features)

['market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'estimated-transaction-volume-usd', 'sma-10-days', 'n-transactions-total', 'blocks-size', 'sma-100-days', 'total-bitcoins']


In [13]:
# Loading correlation matrix features
with open(GDRIVE_LESS_REL_FEATURES, "r") as f:
    less_rel_features = json.load(f)
print(less_rel_features)

['sma-20-days', 'sma-50-days', 'n-unique-addresses', 'difficulty', 'hash-rate', 'avg-block-size', 'transaction-fees-usd', 'trade-volume', 'n-transactions-per-block', 'n-transactions', 'rate-of-change']


## Simple model

In [ ]:
# Get default params
params = parameters.get_defaults_model_params(MODEL_NAME)
params

{'maxIter': [25],
 'regParam': [0],
 'family': ['gaussian'],
 'link': ['identity']}

In [ ]:
# Valid performances with all the features
simple_res_all, simple_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_all

Model    Type      Features  \
0  GeneralizedLinearRegression  simple  all_features   

                    Parameters        RMSE     MAPE         MAE      Variance  \
0  [25, 0, gaussian, identity]  652.944884  0.02302  488.727682  1.055382e+07   

         R2  Adjusted_R2      Time  
0  0.953424     0.953406  2.161118

In [ ]:
utilities.show_results(simple_pred_all, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_res_more_rel, simple_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_more_rel

Model    Type           Features  \
0  GeneralizedLinearRegression  simple  more_rel_features   

                    Parameters        RMSE      MAPE         MAE  \
0  [25, 0, gaussian, identity]  668.329176  0.028191  571.486816   

       Variance        R2  Adjusted_R2      Time  
0  9.815879e+06  0.951204     0.951184  0.838102

In [ ]:
utilities.show_results(simple_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_res_less_rel, simple_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, False)
simple_res_less_rel

Model    Type           Features  \
0  GeneralizedLinearRegression  simple  less_rel_features   

                    Parameters          RMSE      MAPE           MAE  \
0  [25, 0, gaussian, identity]  52046.345821  2.379976  48443.517668   

       Variance         R2  Adjusted_R2      Time  
0  2.731992e+09 -294.92835  -295.044829  0.924372

In [ ]:
utilities.show_results(simple_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Simple model (with data normalization)

In [ ]:
# Valid performances with all the features
simple_norm_res_all, simple_norm_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_all

Model         Type      Features  \
0  GeneralizedLinearRegression  simple_norm  all_features   

                    Parameters         RMSE      MAPE          MAE  \
0  [25, 0, gaussian, identity]  5222.919552  0.188204  4203.750966   

       Variance        R2  Adjusted_R2      Time  
0  2.370982e+07 -1.980113    -1.981521  2.015998

In [ ]:
utilities.show_results(simple_norm_pred_all, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_norm_res_more_rel, simple_norm_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_more_rel

Model         Type           Features  \
0  GeneralizedLinearRegression  simple_norm  more_rel_features   

                    Parameters         RMSE      MAPE          MAE  \
0  [25, 0, gaussian, identity]  7280.716486  0.311021  6268.056469   

       Variance       R2  Adjusted_R2      Time  
0  5.587428e+07 -4.79101    -4.793746  1.061066

In [ ]:
utilities.show_results(simple_norm_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [ ]:
# Valid performances with the corr matrix features
simple_norm_res_less_rel, simple_norm_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL, True)
simple_norm_res_less_rel

Model         Type           Features  \
0  GeneralizedLinearRegression  simple_norm  less_rel_features   

                    Parameters          RMSE      MAPE          MAE  \
0  [25, 0, gaussian, identity]  10404.034352  0.453631  9433.969927   

       Variance         R2  Adjusted_R2      Time  
0  9.149330e+07 -10.825231   -10.830817  1.048709

In [ ]:
utilities.show_results(simple_norm_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Hyperparameter tuning

In [ ]:
choosen_features = all_features
CHOSEN_FEATURES_LABEL = GDRIVE_ALL_FEATURES_NAME

In [ ]:
# Split proportion list
PORTION_LIST = [0.6, 0.7, 0.8, 0.9]

In [ ]:
# Get simple params
params = parameters.get_model_params(MODEL_NAME)
params

{'maxIter': [5, 15, 25, 50, 80],
 'regParam': [0.0, 0.05, 0.1],
 'family': ['gaussian'],
 'link': ['log']}

In [ ]:
hyp_res, hyp_params = utilities.autoTuning(df, choosen_features, params, CHOSEN_FEATURES_LABEL, PORTION_LIST, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
hyp_res

Model        Type      Features  Proportion  \
0  GeneralizedLinearRegression  autotuning  all_features         0.8   

                Parameters         RMSE      MAPE          MAE      Variance  \
0  [5, 0.0, gaussian, log]  2946.199548  0.094743  2529.179178  1.465709e+08   

         R2  Adjusted_R2      Time  
0  0.953033     0.953022  3.536936

## Cross validation

In [ ]:
# Get tuned params
params = hyp_params
params

{'maxIter': [5], 'regParam': [0.0], 'family': ['gaussian'], 'link': ['log']}

In [ ]:
## Cross Validation Parameter
# Multiple Splits Time Series Cross Validation
mul_cv = {'cv_type':'mulTs',
          'kSplits': 5}

# Blocked Time Series Cross Validation
blk_cv = {'cv_type':'blkTs',
          'kSplits': 10}

In [ ]:
mul_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, mul_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
mul_cv_res

Model   Type      Features  Splits Train&Validation  \
0  GeneralizedLinearRegression  mulTs  all_features       1   (21182, 21181)   
1  GeneralizedLinearRegression  mulTs  all_features       2   (42363, 21181)   
2  GeneralizedLinearRegression  mulTs  all_features       3   (63544, 21181)   
3  GeneralizedLinearRegression  mulTs  all_features       4   (84725, 21181)   
4  GeneralizedLinearRegression  mulTs  all_features       5  (105906, 21181)   

                Parameters           RMSE      MAPE           MAE  \
0  [5, 0.0, gaussian, log]    2514.042611  0.178979   1554.389900   
1  [5, 0.0, gaussian, log]    3212.378962  0.542375   2489.675150   
2  [5, 0.0, gaussian, log]    1547.652015  0.143504   1321.301511   
3  [5, 0.0, gaussian, log]  122507.411124  1.903948  88791.624875   
4  [5, 0.0, gaussian, log]    3752.862920  0.153128   3338.606797   

       Variance         R2  Adjusted_R2      Time  
0  1.463922e+07   0.645652     0.645552  3.830779  
1  8.724025e+06  -0.947548    -0.948100  1.909852  
2  1.037798e+06   0.056212     0.055945  4.094188  
3  1.614059e+10 -83.737295   -83.761306  2.401294  
4  4.278871e+07   0.830406     0.830358  2.573717

In [ ]:
blk_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, blk_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
blk_cv_res

Model   Type      Features  Splits Train&Validation  \
0  GeneralizedLinearRegression  blkTs  all_features       1    (10166, 2542)   
1  GeneralizedLinearRegression  blkTs  all_features       2    (10166, 2542)   
2  GeneralizedLinearRegression  blkTs  all_features       3    (10166, 2542)   
3  GeneralizedLinearRegression  blkTs  all_features       4    (10166, 2542)   
4  GeneralizedLinearRegression  blkTs  all_features       5    (10166, 2542)   
5  GeneralizedLinearRegression  blkTs  all_features       6    (10166, 2542)   
6  GeneralizedLinearRegression  blkTs  all_features       7    (10166, 2542)   
7  GeneralizedLinearRegression  blkTs  all_features       8    (10166, 2542)   
8  GeneralizedLinearRegression  blkTs  all_features       9    (10166, 2542)   
9  GeneralizedLinearRegression  blkTs  all_features      10    (10166, 2542)   

                Parameters          RMSE      MAPE          MAE      Variance  \
0  [5, 0.0, gaussian, log]     10.469237  0.013868     8.084320  2.911406e+02   
1  [5, 0.0, gaussian, log]    232.761448  0.060998   148.784409  1.479927e+05   
2  [5, 0.0, gaussian, log]   1747.762985  0.156985  1618.060229  5.722820e+06   
3  [5, 0.0, gaussian, log]    249.593668  0.030853   165.665748  1.941884e+05   
4  [5, 0.0, gaussian, log]    491.478893  0.033251   374.719507  3.626555e+05   
5  [5, 0.0, gaussian, log]    357.530197  0.044164   306.317416  4.897512e+05   
6  [5, 0.0, gaussian, log]  10822.212302  0.244224  8188.664288  7.144469e+07   
7  [5, 0.0, gaussian, log]   4308.473095  0.059059  3117.686276  2.102474e+07   
8  [5, 0.0, gaussian, log]   1400.730984  0.044612  1110.161509  2.099518e+07   
9  [5, 0.0, gaussian, log]   2494.933076  0.086943  2177.470240  7.755560e+06   

         R2  Adjusted_R2      Time  
0  0.702331     0.701627  1.793629  
1  0.799608     0.799134  1.686948  
2 -0.229671    -0.232581  1.198501  
3  0.834359     0.833967  1.150144  
4  0.640305     0.639453  1.105085  
5  0.862403     0.862077  1.336820  
6 -1.405602    -1.411296  2.184626  
7  0.365783     0.364282  1.355856  
8  0.907818     0.907600  1.206280  
9 -0.099386    -0.101988  1.170726

## Comparison table

In [ ]:
# Define what model_info and evaluators in the Model Comparison Table
model_info = ['Model','Type', 'Features', 'Parameters']
evaluator_lst = ['RMSE','MAPE','MAE','Variance','R2','Adjusted_R2','Time']

# The the Cross Validation results would like to compare
comparison_lst = [simple_res_all, simple_res_more_rel, simple_res_less_rel, simple_norm_res_all, simple_norm_res_more_rel, simple_norm_res_less_rel, hyp_res, mul_cv_res, blk_cv_res]

In [ ]:
# Show the Comparison Table
pd.concat([utilities.modelComparison(cv_result, model_info, evaluator_lst) for cv_result in comparison_lst])

Model         Type           Features  \
0  GeneralizedLinearRegression       simple       all_features   
0  GeneralizedLinearRegression       simple  more_rel_features   
0  GeneralizedLinearRegression       simple  less_rel_features   
0  GeneralizedLinearRegression  simple_norm       all_features   
0  GeneralizedLinearRegression  simple_norm  more_rel_features   
0  GeneralizedLinearRegression  simple_norm  less_rel_features   
0  GeneralizedLinearRegression   autotuning       all_features   
0  GeneralizedLinearRegression        mulTs       all_features   
0  GeneralizedLinearRegression        blkTs       all_features   

                    Parameters          RMSE      MAPE           MAE  \
0  [25, 0, gaussian, identity]    652.944884  0.023020    488.727682   
0  [25, 0, gaussian, identity]    668.329176  0.028191    571.486816   
0  [25, 0, gaussian, identity]  52046.345821  2.379976  48443.517668   
0  [25, 0, gaussian, identity]   5222.919552  0.188204   4203.750966   
0  [25, 0, gaussian, identity]   7280.716486  0.311021   6268.056469   
0  [25, 0, gaussian, identity]  10404.034352  0.453631   9433.969927   
0      [5, 0.0, gaussian, log]   2946.199548  0.094743   2529.179178   
0      [5, 0.0, gaussian, log]  26706.869526  0.584387  19499.119646   
0      [5, 0.0, gaussian, log]   2211.594588  0.077496   1721.561394   

       Variance          R2  Adjusted_R2      Time  
0  1.055382e+07    0.953424     0.953406  2.161118  
0  9.815879e+06    0.951204     0.951184  0.838102  
0  2.731992e+09 -294.928350  -295.044829  0.924372  
0  2.370982e+07   -1.980113    -1.981521  2.015998  
0  5.587428e+07   -4.791010    -4.793746  1.061066  
0  9.149330e+07  -10.825231   -10.830817  1.048709  
0  1.465709e+08    0.953033     0.953022  3.536936  
0  3.241557e+09  -16.630515   -16.635511  2.961966  
0  1.281379e+07    0.337795     0.336227  1.418862

## Training the final model

In [15]:
model = utilities.train_final_model(df, choosen_features, params, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)

In [16]:
GDRIVE_MODELS_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/models"
GDRIVE_MODEL_NAME_EXT = GDRIVE_MODELS_DIR + "/" + MODEL_NAME

In [17]:
# Save the trained model
model.write().overwrite().save(GDRIVE_MODEL_NAME_EXT)